In [416]:
import statsmodels.api as sm
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import math
import geopandas as gpd
import os
import pickle as pkl
from shapely.geometry import Point
from multinomial_probit import MultinomialProbitRegression
os.chdir(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\PT_stations')
from functools import partial

# Folium plot of cycle lanes, which are line strings
import folium
from folium.plugins import MarkerCluster

In [417]:
# Read in data 
df = pd.read_excel(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\Roschlau Fellowship\THATS Survey Outputs\1. Collected Data\Sign-Up and Daily Surveys\Sign-Up Survey_September 1_modified.xlsx')

In [418]:
df.columns

Index(['StartDate', 'EndDate', 'Status', 'IPAddress', 'Progress',
       'Duration (in seconds)', 'Finished', 'RecordedDate', 'ResponseId',
       'RecipientLastName',
       ...
       'Q23.1', 'Q24.2', 'Q25.2', 'Q26.2', 'Q27.2', 'Q28.2', 'Q29.2', 'Q30.1',
       'Q31.2', 'Q32.2'],
      dtype='object', length=423)

In [419]:
# Read OSM downloaded file
osm_transport_downloaded = gpd.read_file(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\OSM Analysis\data_unzipped\gis_osm_transport_free_1.shp')
# osm_roads = gdf_roads = gpd.read_file(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\OSM Analysis\data_unzipped\gis_osm_roads_free_1.shp')

Limiting our analysis to just the GTHA

In [420]:
gtha = gpd.read_file(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\OSM Analysis\GTHA_Boundary-shp\GTHA_Boundary.shp')

In [421]:
# Generate a bounding box for the GTHA
gtha_bbox = gtha.total_bounds
gtha_bbox

array([-80.248423,  43.050553, -78.437503,  44.516972])

In [422]:
osm_transport_downloaded_filtered = osm_transport_downloaded.cx[gtha_bbox[0]:gtha_bbox[2], gtha_bbox[1]:gtha_bbox[3]]
osm_transport_downloaded_filtered

osm_id  code           fclass                             name  \
0         21631730  5661   ferry_terminal         Bathurst Street Terminal   
1         25991314  5601  railway_station                              Bay   
2         25991463  5601  railway_station                      Dundas West   
3         26240971  5601  railway_station                      St. Patrick   
4         26240972  5601  railway_station                           Dundas   
...            ...   ...              ...                              ...   
32806  11305593355  5621         bus_stop     Mount Albert Road Stop #5485   
32807  11305593357  5621         bus_stop   Mount Albert Road / Highway 48   
32808  11305593358  5621         bus_stop   Mount Albert Road / Highway 48   
32809  11305593360  5621         bus_stop  King Street / Mount Albert Road   
32810  11305617694  5621         bus_stop     Mount Albert Road Stop #4846   

                         geometry  
0      POINT (-79.39772 43.63387)  
1      POINT (-79.39027 43.67019)  
2      POINT (-79.45297 43.65703)  
3      POINT (-79.38827 43.65482)  
4      POINT (-79.38102 43.65654)  
...                           ...  
32806  POINT (-79.32497 44.12808)  
32807  POINT (-79.31988 44.12869)  
32808  POINT (-79.32042 44.12842)  
32809  POINT (-79.31462 44.13056)  
32810  POINT (-79.31105 44.13182)  

[22034 rows x 5 columns]

In [423]:
# osm_roads_filtered = osm_roads.cx[gtha_bbox[0]:gtha_bbox[2], gtha_bbox[1]:gtha_bbox[3]]
# osm_roads_filtered

In [424]:
# dissemination_areas = gpd.read_file(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\OSM Analysis\Census_DA_s\lda_000b21a_e.shp')
# dissemination_areas

In [425]:
# gtha.crs

In [426]:
# dissemination_areas.to_crs(epsg=4326, inplace=True)

In [427]:
"""dissemination_areas_filtered = dissemination_areas[dissemination_areas.geometry.within(gtha.iloc[0].geometry)]
dissemination_areas_filtered"""

'dissemination_areas_filtered = dissemination_areas[dissemination_areas.geometry.within(gtha.iloc[0].geometry)]\ndissemination_areas_filtered'

Commented out because I'm not analyzing the OSM road network. 

In [428]:
# osm_roads_filtered.crs

In [429]:
"""# Create a new column in dissemination_areas called 'length_of_roads'
dissemination_areas_filtered['km_road_density'] = 0

# Iterate over each row in dissemination_areas
for idx, row in dissemination_areas_filtered.iterrows():
    # Create a buffer of 1km around the polygon
    buffered_polygon = row.geometry.buffer(0.01)
    # Use the overlay method to find LineString geometries that intersect with the buffer
    intersecting_geometries = osm_roads_filtered[osm_roads_filtered.within(buffered_polygon)]
    # Calculate the total length of the intersecting LineString geometries
    total_length = intersecting_geometries['geometry'].length.sum()
    # Calculate density of roads in polygon
    density = total_length / row.geometry.area
    # Assign the density to the 'km_road_density' column
    dissemination_areas_filtered.loc[idx, 'km_road_density'] = density"""


"# Create a new column in dissemination_areas called 'length_of_roads'\ndissemination_areas_filtered['km_road_density'] = 0\n\n# Iterate over each row in dissemination_areas\nfor idx, row in dissemination_areas_filtered.iterrows():\n    # Create a buffer of 1km around the polygon\n    buffered_polygon = row.geometry.buffer(0.01)\n    # Use the overlay method to find LineString geometries that intersect with the buffer\n    intersecting_geometries = osm_roads_filtered[osm_roads_filtered.within(buffered_polygon)]\n    # Calculate the total length of the intersecting LineString geometries\n    total_length = intersecting_geometries['geometry'].length.sum()\n    # Calculate density of roads in polygon\n    density = total_length / row.geometry.area\n    # Assign the density to the 'km_road_density' column\n    dissemination_areas_filtered.loc[idx, 'km_road_density'] = density"

In [430]:
# popns = pd.read_csv(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\OSM Analysis\Population Data\Population Data.csv')
popns = pd.read_csv(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\OSM Analysis\Popn_data.csv')

Making Q13 numeric

In [431]:
# Making Q13 numeric
# Getting all unique values in Q13
df['Q13'].unique()

array(['$20,000-$39,999', '$60,000-$79,999', '$200,000 or more',
       'Under $20,000', '$40,000-$59,999', '$100,000-$124,999',
       '$80,000-$99,999', '$125,000-$149,999', '$150,000-$199,999',
       'Prefer not to answer', nan], dtype=object)

In [432]:
df['Q13'] = df['Q13'].replace({'$20,000-$39,999': (20000+39999)/2, '$60,000-$79,999': (60000+79999)/2, '$40,000-$59,999': (40000+59999)/2, '$100,000-$124,999': (100000+124999)/2, 
                               '$80,000-$99,999': (80000+99999)/2, '$125,000-$149,999': (125000+149999)/2, '$150,000-$199,999': (150000+199999)/2, '$200,000 or more': 200000, 'Under $20,000': 20000,
                               'Prefer not to answer': 84000})

In [433]:
df['Q13'].fillna(84000, inplace=True)

In [434]:
df['Q13'] = df['Q13'].round(0).astype(int)

In [435]:
# Rename the index as 'indivID'
df.index.name = 'indivID'

In [436]:
list(df.columns)

['StartDate',
 'EndDate',
 'Status',
 'IPAddress',
 'Progress',
 'Duration (in seconds)',
 'Finished',
 'RecordedDate',
 'ResponseId',
 'RecipientLastName',
 'RecipientFirstName',
 'RecipientEmail',
 'ExternalReference',
 'LocationLatitude',
 'LocationLongitude',
 'DistributionChannel',
 'UserLanguage',
 'Time_First Click',
 'Time_Last Click',
 'Time_Page Submit',
 'Time_Click Count',
 'Meta_Browser',
 'Meta_Version',
 'Meta_Operating System',
 'Meta_Resolution',
 'Q2',
 'Q3',
 'Q2.1',
 'Q3.1',
 'Q4',
 'Q1',
 'Q1_9_TEXT',
 'Q1-2',
 'Q1-2_9_TEXT',
 'Q2.2',
 'Q3_11',
 'Q4_1',
 'Q5_1',
 'Q6_1',
 'Q7_1',
 'Q8_1',
 'Q9_1',
 'Q10_1',
 'Q11_1',
 'Q12_1',
 'Q13',
 'Q14_1',
 'Q14_2',
 'Q14_3',
 'Q14_4',
 'Q14_5',
 'Q14_6',
 'Q14_7',
 'Q14_8',
 'Q14_9',
 'Q14_10',
 'Q14_11',
 'Q14_12',
 'Q14_13',
 'Q14_11_TEXT',
 'Q1.1',
 'Q2.3',
 'Q3.2',
 'Q4.1',
 'Q5',
 'Q6',
 'Q7',
 'Q8',
 'Q9',
 'Q10_7',
 'Q11_9',
 'Q12_9',
 'Q13_9',
 'Q14_9.1',
 'Q15_9',
 'Q16_9',
 'Q17_9',
 'Q18_9',
 'Q19_9',
 'Q20',
 'Q21

# PT stations

In [437]:
# Read pt stations
pt_stations = gpd.read_file('PT_stations.geojson')

In [438]:
pt_stations.head()

id             @id                            name network  \
0   relation/4803   relation/4803         94A Wellesley Eastbound     TTC   
1  relation/12308  relation/12308  70C O'Connor to Warden Station     TTC   
2  relation/12309  relation/12309        70A O'Connor to Eglinton     TTC   
3  relation/12310  relation/12310                    70B O'Connor     TTC   
4  relation/12312  relation/12312                     87A Cosburn     TTC   

  network:wikidata                         network:wikipedia operator  \
0         Q6612865  en:Toronto Transit Commission bus system      TTC   
1         Q6612865  en:Toronto Transit Commission bus system      TTC   
2         Q6612865  en:Toronto Transit Commission bus system      TTC   
3         Q6612865  en:Toronto Transit Commission bus system      TTC   
4         Q6612865  en:Toronto Transit Commission bus system      TTC   

  operator:wikidata public_transport:version  ref  ... note:name train  \
0            Q17978                        2  94A  ...      None  None   
1            Q17978                        2  70C  ...      None  None   
2            Q17978                        2  70A  ...      None  None   
3            Q17978                     None  70B  ...      None  None   
4            Q17978                        2  87A  ...      None  None   

  construction:light_rail wheeltrans ref:astral platform  \
0                    None       None       None     None   
1                    None       None       None     None   
2                    None       None       None     None   
3                    None       None       None     None   
4                    None       None       None     None   

  check_date:tactile_paving local_ref internet_access:ssid  \
0                      None      None                 None   
1                      None      None                 None   
2                      None      None                 None   
3                      None      None                 None   
4                      None      None                 None   

                                            geometry  
0  MULTILINESTRING ((-79.36952 43.67322, -79.3694...  
1  LINESTRING (-79.32292 43.68439, -79.32289 43.6...  
2  LINESTRING (-79.32292 43.68439, -79.32289 43.6...  
3  MULTILINESTRING ((-79.30181 43.72261, -79.3017...  
4  MULTILINESTRING ((-79.30225 43.68906, -79.3021...  

[5 rows x 145 columns]

In [439]:
# Filter out stations whose geometry is not point type
pt_stations = pt_stations[pt_stations['geometry'].type == 'Point']

In [440]:
subway_stations = pt_stations.loc[(pt_stations['subway'] == 'yes')&(pt_stations['geometry'].type == 'Point')&(pt_stations['wikidata'].notna()), :]

# subway_stations = subway_stations.loc[subway_stations['type'] == 'Point', :]
subway_stations.type.value_counts()

Point    71
dtype: int64

In [441]:
subway_stations

id              @id         name network network:wikidata  \
801     node/25991314    node/25991314          Bay     TTC             None   
804     node/25991463    node/25991463  Dundas West     TTC             None   
805     node/26240971    node/26240971  St. Patrick     TTC             None   
806     node/26240972    node/26240972       Dundas     TTC             None   
813     node/32821214    node/32821214  Main Street     TTC             None   
...               ...              ...          ...     ...              ...   
6678  node/5326548040  node/5326548040     Woodbine     TTC             None   
6680  node/5326551838  node/5326551838      Coxwell     TTC             None   
6682  node/5326558129  node/5326558129    Greenwood     TTC             None   
6683  node/5326559427  node/5326559427     Donlands     TTC             None   
8095  node/8901485524  node/8901485524      Chester     TTC             None   

     network:wikipedia                    operator operator:wikidata  \
801               None  Toronto Transit Commission              None   
804               None  Toronto Transit Commission              None   
805               None  Toronto Transit Commission              None   
806               None  Toronto Transit Commission              None   
813               None  Toronto Transit Commission              None   
...                ...                         ...               ...   
6678              None                        None              None   
6680              None                        None              None   
6682              None                        None              None   
6683              None                        None              None   
8095              None  Toronto Transit Commission              None   

     public_transport:version   ref  ... note:name train  \
801                      None  None  ...      None  None   
804                      None  None  ...      None  None   
805                      None  None  ...      None  None   
806                      None  None  ...      None  None   
813                      None  None  ...      None  None   
...                       ...   ...  ...       ...   ...   
6678                     None  None  ...      None  None   
6680                     None  None  ...      None  None   
6682                     None  None  ...      None  None   
6683                     None  None  ...      None  None   
8095                     None  None  ...      None  None   

     construction:light_rail wheeltrans ref:astral platform  \
801                     None       None       None     None   
804                     None       None       None     None   
805                     None       None       None     None   
806                     None       None       None     None   
813                     None       None       None     None   
...                      ...        ...        ...      ...   
6678                    None       None       None     None   
6680                    None       None       None     None   
6682                    None       None       None     None   
6683                    None       None       None     None   
8095                    None       None       None     None   

     check_date:tactile_paving local_ref internet_access:ssid  \
801                       None      None                 None   
804                       None      None                 None   
805                       None      None                 None   
806                       None      None                 None   
813                       None      None                 None   
...                        ...       ...                  ...   
6678                      None      None                 None   
6680                      None      None                 None   
6682                      None      None                 None   
6683                      None      None                 None   


In [442]:
# Function that calculates the distance between two points using the Haversine formula
def haversine(lon1, lat1, lon2, lat2):
    # Converting the coordinates to radians
    lon1, lat1, lon2, lat2 = map(math.radians, [lon1, lat1, lon2, lat2])
    
    # Calculating the distance
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = math.sin(dlat/2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon/2)**2 
    c = 2 * math.asin(math.sqrt(a)) 
    km = 6367 * c
    
    return km

In [443]:
df['Distance_to_closest_subway_station'] = np.nan
subway_stations['distance'] = np.nan

for idx, row in df.iterrows():
    distance_calc_row = partial(haversine, row.LocationLongitude, row.LocationLatitude)
    subway_stations.loc[:, 'distance'] = subway_stations.apply(lambda x: distance_calc_row(x.geometry.x, x.geometry.y), axis=1)
    # row['haversine_distance'] = gas_stations['distance'].min()
    df.loc[idx, 'Distance_to_closest_subway_station'] = subway_stations['distance'].min()

df['Distance_to_closest_subway_station'].describe()

c:\Users\mwendwa.kiko\Anaconda3\envs\geopandasenv_kiko\lib\site-packages\geopandas\geodataframe.py:1322: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super(GeoDataFrame, self).__setitem__(key, value)
C:\Users\mwendwa.kiko\AppData\Local\Temp\ipykernel_17148\2863632867.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subway_stations.loc[:, 'distance'] = subway_stations.apply(lambda x: distance_calc_row(x.geometry.x, x.geometry.y), axis=1)
C:\Users\mwendwa.kiko\AppData\Local\Temp\ipykernel_17148\2863632867

C:\Users\mwendwa.kiko\AppData\Local\Temp\ipykernel_17148\2863632867.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subway_stations.loc[:, 'distance'] = subway_stations.apply(lambda x: distance_calc_row(x.geometry.x, x.geometry.y), axis=1)
C:\Users\mwendwa.kiko\AppData\Local\Temp\ipykernel_17148\2863632867.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subway_stations.loc[:, 'distance'] = subway_stations.apply(lambda x: distance_calc_row(x.geometry.x, x.geometry.y), axis=1)
C:\Users\mwendwa.kiko\Ap

count     3065.000000
mean        79.986958
std        628.097483
min          0.081725
25%          0.796669
50%          1.822883
75%         16.759604
max      13372.595022
Name: Distance_to_closest_subway_station, dtype: float64

In [444]:
# Fill na with the median
df['Distance_to_closest_subway_station'].fillna(df['Distance_to_closest_subway_station'].median(), inplace=True)

# Cycle lanes

In [445]:
# Read the input file
cycle_lanes = gpd.read_file('Cycle_lanes.geojson')

# Filter out cycle lanes whose geometry is not line type
cycle_lanes = cycle_lanes[cycle_lanes['geometry'].type == 'LineString']

In [446]:
cycle_lanes

id             @id  area     bicycle        foot  \
4         way/3944939     way/3944939  None        None        None   
5         way/3996287     way/3996287  None        None        None   
6         way/3996302     way/3996302  None        None        None   
7         way/3996325     way/3996325  None        None        None   
8         way/3996340     way/3996340  None        None         yes   
...               ...             ...   ...         ...         ...   
10112  way/1209895696  way/1209895696  None  designated  designated   
10113  way/1211634262  way/1211634262  None        None        None   
10114  way/1211634263  way/1211634263  None        None        None   
10115  way/1212150408  way/1212150408  None  designated  designated   
10116  way/1212552955  way/1212552955  None        None        None   

           highway                      name segregated  surface  \
4        secondary            Oriole Parkway       None  asphalt   
5      residential                 Glen Road       None  asphalt   
6      residential                 Glen Road       None  asphalt   
7          primary         Bloor Street East       None  asphalt   
8      residential                 Glen Road       None  asphalt   
...            ...                       ...        ...      ...   
10112     cycleway                      None         no  asphalt   
10113  residential  Pope John Paul II Square       None     None   
10114  residential  Pope John Paul II Square       None     None   
10115         path          Waterfront Trail         no  asphalt   
10116      primary                Highway 7A       None  asphalt   

      abandoned:railway  ... destination:backward destination:forward  \
4                  None  ...                 None                None   
5                  None  ...                 None                None   
6                  None  ...                 None                None   
7                  None  ...                 None                None   
8                  None  ...                 None                None   
...                 ...  ...                  ...                 ...   
10112              None  ...                 None                None   
10113              None  ...                 None                None   
10114              None  ...                 None                None   
10115              None  ...                 None                None   
10116              None  ...                 None                None   

      handrail ramp:bicycle cutting crossing_ref barrier bollard material  \
4         None         None    None         None    None    None     None   
5         None         None    None         None    None    None     None   
6         None         None    None         None    None    None     None   
7         None         None    None         None    None    None     None   
8         None         None    None         None    None    None     None   
...        ...          ...     ...          ...     ...     ...      ...   
10112     None         None    None         None    None    None     None   
10113     None         None    None         None    None    None     None   
10114     None         None    None         None    None    None     None   
10115     None         None    None         None    None    None     None   
10116     None         None    None         None    None    None     None   

                                                geometry  
4      LINESTRING (-79.40123 43.69209, -79.40115 43.6...  
5      LINESTRING (-79.37480 43.67504, -79.37482 43.6...  
6      LINESTRING (-79.37515 43.67762, -79.37518 43.6...  
7      LINESTRING (-79.37084 43.67196, -79.37058 43.6...  
8      LINESTRING (-79.37483 43.67845, -79.37419 43.6...  
...                                                  ...  
10112  LINESTRING (-78.89609 43.94781, -78.89600 43.9...  
10113  LINESTRING (-79.37361 43.89359, -79.37340 43.8...  
10114  LINESTRIN

In [447]:
cycle_lanes.loc[:, 'geometry'].length.sum()

C:\Users\mwendwa.kiko\AppData\Local\Temp\ipykernel_17148\1048337571.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'length' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  cycle_lanes.loc[:, 'geometry'].length.sum()


23.315384898355482

In [448]:
df['Length_of_cycle_lanes_within_radius'] = np.nan

df_sample = df.loc[(df['LocationLongitude'].notna()&(df['LocationLatitude'].notna())), :].sample(100)



for idx, row in df.loc[(df['LocationLongitude'].notna()&(df['LocationLatitude'].notna())), :].iterrows():
    # Create a buffer of 1km around the point
    buffered_point = Point.buffer(Point(row.LocationLongitude, row.LocationLatitude), 0.05)
    # Use the intersection method to find LineString geometries that intersect with the buffer
    intersecting_geometries = cycle_lanes[cycle_lanes.within(buffered_point)]

    # Calculate the total length of the intersecting LineString geometries
    total_length = intersecting_geometries['geometry'].length.sum()

    # Assign the total length to the corresponding row in the input file
    df.loc[idx, 'Length_of_cycle_lanes_within_radius'] = total_length

C:\Users\mwendwa.kiko\AppData\Local\Temp\ipykernel_17148\1515151482.py:14: UserWarning: Geometry is in a geographic CRS. Results from 'length' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  total_length = intersecting_geometries['geometry'].length.sum()
C:\Users\mwendwa.kiko\AppData\Local\Temp\ipykernel_17148\1515151482.py:14: UserWarning: Geometry is in a geographic CRS. Results from 'length' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  total_length = intersecting_geometries['geometry'].length.sum()
C:\Users\mwendwa.kiko\AppData\Local\Temp\ipykernel_17148\1515151482.py:14: UserWarning: Geometry is in a geographic CRS. Results from 'length' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  total_length = intersecting_geometries['geometry'].length.sum()
C:\Users\mwendwa.kiko\AppDat

## Bus Stations

In [449]:
bus_stations = osm_transport_downloaded_filtered.loc[osm_transport_downloaded_filtered['fclass'] == 'bus_stop', :].copy()
bus_stations

osm_id  code    fclass                             name  \
58       206739584  5621  bus_stop                             None   
59       207730093  5621  bus_stop                             None   
60       207730120  5621  bus_stop  Meadowlands Terminal Platform 1   
62       238753589  5621  bus_stop                 St George Street   
63       238753600  5621  bus_stop                 St George Street   
...            ...   ...       ...                              ...   
32806  11305593355  5621  bus_stop     Mount Albert Road Stop #5485   
32807  11305593357  5621  bus_stop   Mount Albert Road / Highway 48   
32808  11305593358  5621  bus_stop   Mount Albert Road / Highway 48   
32809  11305593360  5621  bus_stop  King Street / Mount Albert Road   
32810  11305617694  5621  bus_stop     Mount Albert Road Stop #4846   

                         geometry  
58     POINT (-79.92900 43.23333)  
59     POINT (-79.93012 43.23406)  
60     POINT (-79.94477 43.22739)  
62     POINT (-79.39862 43.66387)  
63     POINT (-79.39823 43.66424)  
...                           ...  
32806  POINT (-79.32497 44.12808)  
32807  POINT (-79.31988 44.12869)  
32808  POINT (-79.32042 44.12842)  
32809  POINT (-79.31462 44.13056)  
32810  POINT (-79.31105 44.13182)  

[21107 rows x 5 columns]

In [450]:
df['LocationLongitude'].isna().sum()

1714

In [451]:
df['Distance_to_closest_bus_station'] = np.nan
bus_stations['distance'] = np.nan

for idx, row in df.loc[(df['LocationLongitude'].notna()&(df['LocationLatitude'].notna())), :].iterrows():
    buffered_point = Point.buffer(Point(row.LocationLongitude, row.LocationLatitude), 0.1)
    # Use the intersection method to find LineString geometries that intersect with the buffer
    intersecting_geometries = bus_stations[bus_stations.within(buffered_point)]

    distance_calc_row = partial(haversine, row.LocationLongitude, row.LocationLatitude)
    intersecting_geometries.loc[:, 'distance'] = intersecting_geometries.apply(lambda x: distance_calc_row(x.geometry.x, x.geometry.y), axis=1)
    # row['haversine_distance'] = gas_stations['distance'].min()
    df.loc[idx, 'Distance_to_closest_bus_station'] = intersecting_geometries['distance'].min()

df['Distance_to_closest_bus_station'].describe()

C:\Users\mwendwa.kiko\AppData\Local\Temp\ipykernel_17148\1993303723.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  intersecting_geometries.loc[:, 'distance'] = intersecting_geometries.apply(lambda x: distance_calc_row(x.geometry.x, x.geometry.y), axis=1)
C:\Users\mwendwa.kiko\AppData\Local\Temp\ipykernel_17148\1993303723.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  intersecting_geometries.loc[:, 'distance'] = intersecting_geometries.apply(lambda x: distance_calc_row(x.geometry.x, x.geometry.y)

count    2908.000000
mean        0.316375
std         0.575728
min         0.040424
25%         0.121602
50%         0.170875
75%         0.310941
max        10.035760
Name: Distance_to_closest_bus_station, dtype: float64

In [452]:
df_sample['Length_of_cycle_lanes_within_radius'].describe()

count    0.0
mean     NaN
std      NaN
min      NaN
25%      NaN
50%      NaN
75%      NaN
max      NaN
Name: Length_of_cycle_lanes_within_radius, dtype: float64

In [453]:
# sns.distplot(df_sample['Length_of_cycle_lanes_within_radius'])

In [454]:


# Create a map object
m = folium.Map(location=[43.6532, -79.3832], zoom_start=10)

# Add the shapefile to the map
folium.GeoJson(cycle_lanes).add_to(m)

# Display the map
m

# Save the map
m.save('cycle_lanes.html')

Distance between home location and CBD

In [455]:
# Code that calculates the distance between ('start_loc_lon', 'start_loc_lat') and ('end_loc_lon', 'end_loc_lat') and adds it to the dataframe
# The distance is calculated using the Haversine formula
# The distance is calculated in km
# The distance is added to the dataframe as a new column called 'distance'

# Function that calculates the distance between two points using the Haversine formula
def haversine(lon1, lat1, lon2, lat2):
    # Converting the coordinates to radians
    lon1, lat1, lon2, lat2 = map(math.radians, [lon1, lat1, lon2, lat2])
    
    # Calculating the distance
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = math.sin(dlat/2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon/2)**2 
    c = 2 * math.asin(math.sqrt(a)) 
    km = 6367 * c
    
    return km

In [456]:
# Calculating the distance to the coordinates 43.6492° N, 79.3795° W
distance_calc_row = partial(haversine, -79.3795, 43.6492)
df['Distance_to_scotiabank_tower'] = df.apply(lambda x: distance_calc_row(x.LocationLongitude, x.LocationLatitude), axis=1)

Creating df_reduced

In [457]:
# Add a new column 'Medium_number' = count of 'Medium to large car (e.g., Toyota Camry or Audi A4)' in columns Q50.1, Q51.1, Q52
def count_medium(row, name):
    count = 0
    for i in row:
        if i == name:
            count += 1
    return count

df['Medium_number'] = df[['Q50.1', 'Q51.1', 'Q52']].apply(count_medium, name='Medium to large car (e.g., Toyota Camry or Audi A4)', axis=1)

df['Medium_number'].sum()

df['Small_number'] = df[['Q50.1', 'Q51.1', 'Q52']].apply(count_medium, name='Small car (e.g., Fiat 500 or Volkswagen Polo)', axis=1)
df['Small_number'].sum()

df['Off_road_number'] = df[['Q50.1', 'Q51.1', 'Q52']].apply(count_medium, name='Off-road vehicle (e.g., Landrover Discovery)', axis=1)
df['Off_road_number'].sum()

df['Luxury_number'] = df[['Q50.1', 'Q51.1', 'Q52']].apply(count_medium, name='Luxury car or sports coupe (e.g., Mercedes-Benz E-Class, BMW 7 Series or Porsche 911)', axis=1)
df['Luxury_number'].sum()

df['Van_number'] = df[['Q50.1', 'Q51.1', 'Q52']].apply(count_medium, name='Minivan or van (e.g., Honda Odyssey)', axis=1)
df['Van_number'].sum()

279

Count parking spots

In [458]:
df['Q59.1'].unique()

array(['Residential underground parking ', nan, 'Garage ', 'Driveway',
       'Surface lot', 'Residential on-street parking ', 'Other ',
       'Indoor public parking '], dtype=object)

In [459]:
df['Residential_underground_number'] = df[['Q59.1', 'Q60.1', 'Q61.1', 'Q62.1', 'Q63', 'Q64.1', 'Q65.1', 'Q66.1']].apply(count_medium, name='Residential underground parking ', axis=1)
print(df['Residential_underground_number'].describe())
df['Garage_number'] = df[['Q59.1', 'Q60.1', 'Q61.1', 'Q62.1', 'Q63', 'Q64.1', 'Q65.1', 'Q66.1']].apply(count_medium, name='Garage ', axis=1)
print(df['Garage_number'].describe())	
df['Surface_lot_number'] = df[['Q59.1', 'Q60.1', 'Q61.1', 'Q62.1', 'Q63', 'Q64.1', 'Q65.1', 'Q66.1']].apply(count_medium, name='Surface lot', axis=1)
print(df['Surface_lot_number'].describe())
df['Residential_on_street_number'] = df[['Q59.1', 'Q60.1', 'Q61.1', 'Q62.1', 'Q63', 'Q64.1', 'Q65.1', 'Q66.1']].apply(count_medium, name='Residential on-street parking ', axis=1)
print(df['Residential_on_street_number'].describe())
df['Indoor_public_number'] = df[['Q59.1', 'Q60.1', 'Q61.1', 'Q62.1', 'Q63', 'Q64.1', 'Q65.1', 'Q66.1']].apply(count_medium, name='Indoor public parking ', axis=1)
print(df['Indoor_public_number'].describe())

count    4779.000000
mean        0.199623
std         0.483196
min         0.000000
25%         0.000000
50%         0.000000
75%         0.000000
max         8.000000
Name: Residential_underground_number, dtype: float64
count    4779.000000
mean        0.325173
std         0.652888
min         0.000000
25%         0.000000
50%         0.000000
75%         0.000000
max         8.000000
Name: Garage_number, dtype: float64
count    4779.000000
mean        0.032015
std         0.206681
min         0.000000
25%         0.000000
50%         0.000000
75%         0.000000
max         3.000000
Name: Surface_lot_number, dtype: float64
count    4779.000000
mean        0.048755
std         0.262662
min         0.000000
25%         0.000000
50%         0.000000
75%         0.000000
max         5.000000
Name: Residential_on_street_number, dtype: float64
count    4779.000000
mean        0.002302
std         0.055983
min         0.000000
25%         0.000000
50%         0.000000
75%         0.000000


In [460]:
df['Q58.1'].unique()

array([1, '0 (no parking spots)', 3, 2, 6, 4, '8 or more', nan, 5, 7],
      dtype=object)

In [461]:
# Parking cost
df['Parking_cost_per_slot'] = (df[['Q83.1', 'Q84.1', 'Q85', 'Q86.1', '87', 'Q88.1', 'Q89.1', 'Q90.1']].sum(axis=1) 
                               / df[['Residential_underground_number', 'Garage_number', 'Surface_lot_number', 'Residential_on_street_number', 'Indoor_public_number']].sum(axis=1)).fillna(0)

# Replace infinity values with 0
df['Parking_cost_per_slot'] = df['Parking_cost_per_slot'].replace([np.inf, -np.inf], 0)
                               

In [462]:
# Add a new column to df with the value 1 if Q42-2, Q43-2, or Q44-2 != 'Gasoline'
df['Gasoline'] = df[['Q42-2', 'Q43-2', 'Q44-2']].apply(lambda x: 1 if x[0] != 'Gasoline' or x[1] != 'Gasoline' or x[2] != 'Gasoline' else 0, axis=1)
df['Gasoline'].value_counts()

1    4651
0     128
Name: Gasoline, dtype: int64

In [463]:
df_reduced = df[['Q13', 'Q3_11', 'Q14_12', 'Q8', 'Medium_number', 'Small_number', 'Off_road_number', 'Luxury_number', 'Van_number', 
                 'Distance_to_scotiabank_tower', 'Q43.1', 'Gasoline', 'Residential_underground_number', 'Garage_number', 
                 'Surface_lot_number', 'Residential_on_street_number', 'Indoor_public_number', 'Parking_cost_per_slot', 'Distance_to_closest_subway_station', 
                 'Length_of_cycle_lanes_within_radius', 'Distance_to_closest_bus_station']].copy()
df_reduced.isna().sum()

Q13                                       0
Q3_11                                  1513
Q14_12                                 1547
Q8                                     1548
Medium_number                             0
Small_number                              0
Off_road_number                           0
Luxury_number                             0
Van_number                                0
Distance_to_scotiabank_tower           1714
Q43.1                                  1582
Gasoline                                  0
Residential_underground_number            0
Garage_number                             0
Surface_lot_number                        0
Residential_on_street_number              0
Indoor_public_number                      0
Parking_cost_per_slot                     0
Distance_to_closest_subway_station        0
Length_of_cycle_lanes_within_radius    1714
Distance_to_closest_bus_station        1871
dtype: int64

In [464]:
# Save to excel C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\R_code\Sign-Up_small_c.xlsx
# df_reduced.to_excel(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\R_code\Sign-Up_ordered_few_cols.xlsx', index=False)

In [465]:
df_reduced['Q43.1'] = df_reduced['Q43.1'].replace({'0 (no cars in my household)': 0})

In [466]:
df_reduced['Q43.1'].value_counts()

1.0    1489
0.0     780
2.0     759
3.0     126
4.0      30
5.0      12
7.0       1
Name: Q43.1, dtype: int64

In [467]:
df_reduced = df_reduced.rename(columns={'Q43.1': 'Number_cars'})

In [468]:
df_reduced['Number_cars_level'] = df_reduced['Number_cars'].replace({5: 4, 6: 4, 7: 4})

In [469]:
df_reduced['Q3_11'].fillna(2.4, inplace=True)

In [470]:
df_reduced.isna().sum()

Q13                                       0
Q3_11                                     0
Q14_12                                 1547
Q8                                     1548
Medium_number                             0
Small_number                              0
Off_road_number                           0
Luxury_number                             0
Van_number                                0
Distance_to_scotiabank_tower           1714
Number_cars                            1582
Gasoline                                  0
Residential_underground_number            0
Garage_number                             0
Surface_lot_number                        0
Residential_on_street_number              0
Indoor_public_number                      0
Parking_cost_per_slot                     0
Distance_to_closest_subway_station        0
Length_of_cycle_lanes_within_radius    1714
Distance_to_closest_bus_station        1871
Number_cars_level                      1582
dtype: int64

In [471]:
# Drop na values
## df_reduced.dropna(inplace=True)

The size of the salary term was causing issues with the estimation

In [472]:
# df_reduced['Q13'] /= 1000
df_reduced['Q13'] = np.log(df_reduced['Q13'])

In [473]:
df_reduced['Log_distance_to_scotia_plaza'] = np.log(df_reduced['Distance_to_scotiabank_tower'])

In [474]:
# Save to excel C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\R_code\Sign-Up_small_c.xlsx
# df_reduced.to_excel(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\R_code\Sign-Up_ordered.xlsx', index=False)

# Adding commute numbers info

In [475]:
# Import the PCCF file 
pccf = pd.read_spss(r"C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\TraderCanada\StatsCan Data\pccf_fccp_V2212_2021.sav")

pccf

PC  FSA            PR            CDuid     CSDuid      CSDname  \
0        A0A0E8  A0A  Newfoundland  Division No.  1  1001446.0       Brigus   
1        A0A1G0  A0A  Newfoundland  Division No.  1  1001409.0  Bay Roberts   
2        A0A1K0  A0A  Newfoundland  Division No.  1  1001446.0       Brigus   
3        A0A2H0  A0A  Newfoundland  Division No.  1  1001149.0    Ferryland   
4        A0A3J0  A0A  Newfoundland  Division No.  1  1001409.0  Bay Roberts   
...         ...  ...           ...              ...        ...          ...   
1368848  Y1A4S4  Y1A         Yukon            Yukon  6001009.0   Whitehorse   
1368849  Y1A4V4  Y1A         Yukon            Yukon  6001009.0   Whitehorse   
1368850  Y1A5K2  Y1A         Yukon            Yukon  6001009.0   Whitehorse   
1368851  Y1A5R2  Y1A         Yukon            Yukon  6001009.0   Whitehorse   
1368852  Y1A6L1  Y1A         Yukon            Yukon  6001009.0   Whitehorse   

        CSDtype  CCScode                                                SAC  \
0          Town    472.0  Moderate metropolitan influenced zone/Zone d'i...   
1          Town    304.0  Moderate metropolitan influenced zone/Zone d'i...   
2          Town    472.0  Moderate metropolitan influenced zone/Zone d'i...   
3          Town    214.0  Moderate metropolitan influenced zone/Zone d'i...   
4          Town    304.0  Moderate metropolitan influenced zone/Zone d'i...   
...         ...      ...                                                ...   
1368848    City     45.0                                         Whitehorse   
1368849    City     45.0                                         Whitehorse   
1368850    City     45.0                                         Whitehorse   
1368851    City     45.0                                         Whitehorse   
1368852    City     45.0                                         Whitehorse   

                                  SACtype  ...  \
0              Moderately influenced zone  ...   
1              Moderately influenced zone  ...   
2              Moderately influenced zone  ...   
3              Moderately influenced zone  ...   
4              Moderately influenced zone  ...   
...                                   ...  ...   
1368848  Non-tracted census agglomeration  ...   
1368849  Non-tracted census agglomeration  ...   
1368850  Non-tracted census agglomeration  ...   
1368851  Non-tracted census agglomeration  ...   
1368852  Non-tracted census agglomeration  ...   

                                             PCtype      Comm_Name  \
0                                   Post office box         BRIGUS   
1                 Street address with route service    BAY ROBERTS   
2                                  General Delivery         BRIGUS   
3                                   Post office box      FERRYLAND   
4                                   Post office box  PORT DE GRAVE   
...                                             ...            ...   
1368848  Street address with letter carrier service     WHITEHORSE   
1368849  Street address with letter carrier service     WHITEHORSE   
1368850  Street address with letter carrier service     WHITEHORSE   
1368851  Street address with letter carrier service     WHITEHORSE   
1368852  Street address with letter carrier service     WHITEHORSE   

                                                       DMT H_DMT Birth_Date  \
0        Rural postal codes (the second digit of the po...     W   20130806   
1        Rural postal codes (the second digit of the po...     W   19921220   
2        Rural postal codes (the second digit of the po...     W   19921220   
3        Rural postal codes (the second digit of the po...     W   19921220   
4        Rural postal codes (the second digit of the po...     W   19921220   
...                                                    ...   ...        ...   
1368848                      Delivery to blockface address     A   19921220   
1368849                      Delivery to 

In [476]:
df_copy = df.copy()

In [477]:
pccf_copy = pccf.copy()

In [478]:
pccf['SLI'].value_counts()

flag one record of an active postal code    885284
indicates an additional record              483569
Name: SLI, dtype: int64

In [479]:

# STEP 2: Prepare for merge 

# Keep only the postal codes that have a Single Link Indicator (SLI) value of 1 in pccf 
pccf = pccf[pccf['SLI']=='flag one record of an active postal code'] 

# Rename the postal code variables in mydataset and pccf pcode 
df_copy = df_copy.rename({'Q2.2':'pcode'}, axis=1) 
pccf = pccf.rename(columns={pccf.columns[0] : 'pcode'}) 


In [480]:
pccf.pcode

0          A0A0E8
3          A0A2H0
4          A0A3J0
5          A0A4G0
9          A0C0C4
            ...  
1368847    Y1A4R9
1368848    Y1A4S4
1368849    Y1A4V4
1368850    Y1A5K2
1368852    Y1A6L1
Name: pcode, Length: 885284, dtype: object

In [481]:
# Remove spaces from df_copy['pcode']
df_copy['pcode'] = df_copy['pcode'].str.replace(' ', '')

In [482]:
# Make all letters in df_copy['pcode'] uppercase
df_copy['pcode'] = df_copy['pcode'].str.upper()

In [483]:
# Replace '-' with a space in df_copy['pcode']
df_copy['pcode'] = df_copy['pcode'].str.replace('-', '')

In [484]:
df_copy = df_copy.merge(pccf, on='pcode', how='left')

In [485]:
# df_copy.to_excel('Sign-Up_ordered_with_pccf.xlsx')

Adding census data

In [486]:
census_commute_data = pd.read_csv(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\Commuting_method\Commuting_method_data.csv')

In [487]:
df_copy = df_copy.rename({'DAuid':'dauid'}, axis=1)
census_commute_data = census_commute_data.rename({'COL0':'dauid'}, axis=1) 

In [488]:
df_copy = df_copy.merge(census_commute_data, on='dauid', how='left')

In [489]:
df_copy['Car_driver_mode_share'] = df_copy['COL3'] / df_copy['COL1']
df_copy['Car_passenger_mode_share'] = df_copy['COL4'] / df_copy['COL1']
df_copy['Public_transit_mode_share'] = df_copy['COL5'] / df_copy['COL1']
df_copy['Walk_mode_share'] = df_copy['COL6'] / df_copy['COL1']
df_copy['Bike_mode_share'] = df_copy['COL7'] / df_copy['COL1']

In [490]:
df_copy.index.name = 'indivID'

In [491]:
# Population per dauid
df_copy.groupby('dauid').size().sort_values(ascending=False)

dauid
35204004.0    16
35204922.0    14
35203157.0    13
35204650.0    13
35204606.0    12
              ..
35201863.0     1
35201861.0     1
35201860.0     1
35201851.0     1
59090069.0     1
Length: 2153, dtype: int64

Adding census data - dwelling type

In [492]:
census_dwelling_type = pd.read_csv(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\Commuting_method\Dwelling_and_other_data.csv')
census_dwelling_type

COL0      COL1     COL2    COL3    COL4     COL5    COL6   COL7  \
0          1001  117180.0  74485.0  4575.0  6740.0  22585.0  7725.0  555.0   
1      10010165     220.0    105.0     0.0     0.0    105.0     5.0    0.0   
2      10010166     145.0     80.0     0.0     0.0     70.0     0.0    0.0   
3      10010167     185.0     75.0     0.0     0.0    110.0     0.0    0.0   
4      10010168     250.0    110.0     0.0     0.0    135.0     0.0    0.0   
...         ...       ...      ...     ...     ...      ...     ...    ...   
58224  62080024     140.0     85.0     5.0    50.0      0.0     0.0    0.0   
58225  62080025     150.0     55.0    10.0    85.0      0.0     5.0    0.0   
58226  62080026     250.0    125.0     0.0   125.0      0.0     0.0    0.0   
58227  62080027     170.0     75.0    15.0    80.0      0.0     0.0    0.0   
58228  62080028     120.0     60.0    25.0    35.0      0.0     0.0    0.0   

        COL8   COL9  ...   COL56   COL57     COL58     COL59    COL60  COL61  \
0      190.0  330.0  ...  1070.0  1240.0  300000.0  305600.0  31295.0   18.6   
1        0.0    0.0  ...  1620.0  1500.0  348000.0  350000.0     75.0    0.0   
2        0.0    0.0  ...   660.0  1080.0  332000.0  340000.0     45.0    0.0   
3        0.0    0.0  ...   810.0  1140.0  324000.0  350000.0     45.0    0.0   
4        0.0    0.0  ...  1060.0  1330.0  300000.0  312000.0     70.0    0.0   
...      ...    ...  ...     ...     ...       ...       ...      ...    ...   
58224    0.0    0.0  ...  1330.0  1650.0  348000.0  370000.0     80.0   68.8   
58225    0.0    0.0  ...   725.0   950.0  234000.0  240000.0    120.0   87.5   
58226    0.0    0.0  ...   940.0  1120.0  224000.0  240000.0    195.0   87.2   
58227    0.0    0.0  ...   632.0   720.0  200000.0  180000.0    140.0   92.9   
58228    0.0    0.0  ...     NaN  1000.0       NaN  240000.0    105.0   90.5   

       COL62  COL63   COL64   COL65  
0       33.8   21.8   930.0   970.0  
1       26.7    0.0   950.0  1000.0  
2        0.0    0.0   795.0   880.0  
3        0.0    0.0   750.0   760.0  
4        0.0    0.0  1100.0  1000.0  
...      ...    ...     ...     ...  
58224    0.0   31.3   448.0  1000.0  
58225    0.0   37.5   151.0   470.0  
58226    5.1   41.0   131.0   512.0  
58227    0.0   57.1   184.0   470.0  
58228    0.0   33.3   143.0   510.0  

[58229 rows x 66 columns]

In [493]:

census_dwelling_type = census_dwelling_type.rename({'COL0':'dauid'}, axis=1) 

In [494]:
df_copy = df_copy.merge(census_dwelling_type, on='dauid', how='left')

In [495]:
df_copy = df_copy.rename(columns={'COL64': 'Median_rent', 'COL65': 'Average_rent', 'COL56': 'Median_mortgage', 'COL57': 'Average_mortgage'})

In [496]:
df_copy

StartDate             EndDate      Status        IPAddress  \
0    2023-04-29 18:59:31 2023-04-29 19:08:47  IP Address     99.231.84.16   
1    2023-04-29 20:55:34 2023-04-29 20:59:15  IP Address   72.143.204.255   
2    2023-04-30 11:02:18 2023-04-30 11:06:50  IP Address   72.137.116.243   
3    2023-04-30 15:24:56 2023-04-30 15:32:43  IP Address    99.231.94.199   
4    2023-04-30 11:49:53 2023-04-30 16:29:12  IP Address  174.119.234.214   
...                  ...                 ...         ...              ...   
4774 2023-07-05 19:12:36 2023-07-05 22:16:14  IP Address     99.237.57.17   
4775 2023-07-05 13:10:45 2023-07-05 13:20:07  IP Address  209.195.255.116   
4776 2023-07-05 14:47:11 2023-07-05 14:52:18  IP Address       70.27.38.4   
4777 2023-07-05 21:56:55 2023-07-05 22:01:57  IP Address      76.64.72.15   
4778 2023-07-05 20:28:10 2023-07-06 08:22:03  IP Address      45.74.68.62   

      Progress  Duration (in seconds)  Finished        RecordedDate  \
0          100                    555      True 2023-04-29 19:08:48   
1          100                    220      True 2023-04-29 20:59:17   
2          100                    272      True 2023-04-30 11:06:52   
3          100                    466      True 2023-04-30 15:32:46   
4          100                  16759      True 2023-04-30 16:29:14   
...        ...                    ...       ...                 ...   
4774         7                  11018     False 2023-07-06 15:25:48   
4775        92                    561     False 2023-07-06 15:25:48   
4776         4                    307     False 2023-07-06 15:25:48   
4777         1                    301     False 2023-07-06 15:25:48   
4778        66                  42833     False 2023-07-06 15:25:48   

             ResponseId RecipientLastName  ... Median_mortgage  \
0     R_3iCGZqw0ZCmvOiH              Dong  ...          1420.0   
1     R_2ydBSPfhVa9Xp9a          Haghighi  ...          2480.0   
2     R_3nSDCR0qpho4aUV          Berahman  ...             NaN   
3     R_1IfLn2qE0EtYj8k            Miller  ...          1030.0   
4     R_3JfKOi352bZpaOO                Xu  ...          2480.0   
...                 ...               ...  ...             ...   
4774  R_28ZY4oLKm8ylCoO               NaN  ...          2600.0   
4775  R_2zHLHHPzTE70cn7               NaN  ...          1360.0   
4776  R_1r6tuNwqiES1mja               NaN  ...          1220.0   
4777  R_przpTXnk99vKQFz               NaN  ...             NaN   
4778  R_2ONrqrIogSJdnZz               NaN  ...          2240.0   

     Average_mortgage      COL58      COL59  COL60 COL61 COL62  COL63  \
0              1840.0   980000.0  1000000.0   40.0   0.0   NaN    0.0   
1              2480.0   900000.0  1040000.0  190.0   0.0  47.4    0.0   
2                 NaN        NaN        NaN  320.0   0.0  39.1   31.1   
3              2400.0  1510000.0  1640000.0  125.0   0.0  60.0   32.0   
4              2480.0   900000.0  1040000.0  190.0   0.0  47.4    0.0   
...               ...        ...        ...    ...   ...   ...    ...   
4774           2880.0  1800000.0  1920000.0   80.0   0.0  31.3   42.9   
4775           1840.0  1200000.0  1260000.0   70.0   0.0   0.0    0.0   
4776           1900.0  1700000.0  1660000.0    0.0   NaN   NaN    NaN   
4777              NaN        NaN        NaN    NaN   NaN   NaN    NaN   
4778           2120.0  1110000.0  1200000.0   20.0   0.0   0.0    0.0   

      Median_rent  Average_rent  
0          2880.0        2400.0  
1          2500.0        2400.0  
2          1450.0        1480.0  
3          1940.0        1920.0  
4          2500.0        2400.0  
...           ...           ...  
4774       1250.0        1400.0  
4775       1720.0        1850.0  
4776          NaN           NaN  
4777          NaN           NaN  
4778          NaN        2800.0  

[4779 rows x 548 columns]

In [497]:
df_copy[['Median_rent', 'Average_rent', 'Median_mortgage', 'Average_mortgage']]

Median_rent  Average_rent  Median_mortgage  Average_mortgage
0          2880.0        2400.0           1420.0            1840.0
1          2500.0        2400.0           2480.0            2480.0
2          1450.0        1480.0              NaN               NaN
3          1940.0        1920.0           1030.0            2400.0
4          2500.0        2400.0           2480.0            2480.0
...           ...           ...              ...               ...
4774       1250.0        1400.0           2600.0            2880.0
4775       1720.0        1850.0           1360.0            1840.0
4776          NaN           NaN           1220.0            1900.0
4777          NaN           NaN              NaN               NaN
4778          NaN        2800.0           2240.0            2120.0

[4779 rows x 4 columns]

In [498]:
# Fill na median values with the median of the column and average values with the average of the column
df_copy['Median_rent'].fillna(df_copy['Median_rent'].median(), inplace=True)
df_copy['Average_rent'].fillna(df_copy['Average_rent'].mean(), inplace=True)
df_copy['Median_mortgage'].fillna(df_copy['Median_mortgage'].median(), inplace=True)
df_copy['Average_mortgage'].fillna(df_copy['Average_mortgage'].mean(), inplace=True)

In [499]:
# Convert rent and mortgage to log
df_copy['Log_median_rent'] = np.log(df_copy['Median_rent'])
df_copy['Log_average_rent'] = np.log(df_copy['Average_rent'])
df_copy['Log_median_mortgage'] = np.log(df_copy['Median_mortgage'])
df_copy['Log_average_mortgage'] = np.log(df_copy['Average_mortgage'])

Adding dwelling data and population density data

In [500]:
# Read dataset of popn density per and dwelling characteristics per dauid
census_dwelling_type = pd.read_csv(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\WSTLUR 2023\Additional census data\Dwelling and density.csv')
census_dwelling_type

COL0  COL1     COL2    COL3      COL4     COL5    COL6    COL7  \
0          1001     0  9104.58    29.9  117180.0  74485.0  4575.0  6740.0   
1      10010165   165     0.38  1309.9     220.0    105.0     0.0     0.0   
2      10010166   166     0.10  3563.9     145.0     80.0     0.0     0.0   
3      10010167   167     0.13  3217.4     185.0     75.0     0.0     0.0   
4      10010168   168     0.19  2736.8     250.0    110.0     0.0     0.0   
...         ...   ...      ...     ...       ...      ...     ...     ...   
58224  62080024    24     0.40  1055.9     140.0     85.0     5.0    50.0   
58225  62080025    25   287.39     1.8     150.0     55.0    10.0    85.0   
58226  62080026    26   251.60     3.4     250.0    125.0     0.0   125.0   
58227  62080027    27    24.65    31.5     170.0     75.0    15.0    80.0   
58228  62080028    28     3.90   146.9     120.0     60.0    25.0    35.0   

          COL8    COL9  ...  COL12     COL13    COL14    COL15    COL16  \
0      22585.0  7725.0  ...  330.0  117175.0  19265.0  32635.0  17230.0   
1        105.0     5.0  ...    0.0     230.0     10.0     75.0    135.0   
2         70.0     0.0  ...    0.0     125.0      0.0     70.0     40.0   
3        110.0     0.0  ...    0.0     190.0      0.0     60.0     90.0   
4        135.0     0.0  ...    0.0     275.0     10.0    120.0    115.0   
...        ...     ...  ...    ...       ...      ...      ...      ...   
58224      0.0     0.0  ...    0.0     140.0      0.0     50.0     25.0   
58225      0.0     5.0  ...    0.0     150.0     10.0     40.0     40.0   
58226      0.0     0.0  ...    0.0     250.0     15.0     60.0     35.0   
58227      0.0     0.0  ...    0.0     170.0     10.0     40.0     30.0   
58228      0.0     0.0  ...    0.0     120.0      0.0     25.0     40.0   

         COL17   COL18   COL19    COL20   COL21  
0      14260.0  7855.0  9595.0  10500.0  5855.0  
1         10.0     0.0     0.0      0.0     0.0  
2         10.0     0.0     0.0      0.0     0.0  
3         20.0     0.0     0.0     10.0     0.0  
4         15.0     0.0     0.0      0.0     0.0  
...        ...     ...     ...      ...     ...  
58224     45.0    10.0     0.0      0.0    10.0  
58225     30.0    10.0     0.0     10.0    10.0  
58226     45.0    25.0    30.0     35.0    10.0  
58227     35.0    10.0    20.0     15.0    25.0  
58228     30.0     0.0    10.0      0.0    10.0  

[58229 rows x 22 columns]

In [501]:
# Adding suffix '_09_12' to all other columns
census_dwelling_type = census_dwelling_type.add_suffix('_09_12')

census_dwelling_type = census_dwelling_type.rename({'COL0_09_12':'dauid', 'COL3_09_12': 'Popn_density',
                                                    }, axis=1)



In [502]:
# Add columns COL0 to COL21 to df_copy
df_copy = df_copy.merge(census_dwelling_type, left_on='dauid', right_on='dauid', how='left')

In [503]:
# Rename columns as COL14_09_12: 1940-1960, COL15_09_12: 1961-1980, COL16_09_12: 1981-1990, 
# COL17_09_12: 1991-2000, COL18_09_12: 2001-2005, COL19_09_12: 2006-2010, COL20_09_12: 2011-2015, COL21_09_12: 2016-2021
df_copy = df_copy.rename(columns={'COL14_09_12': '1940-1960', 'COL15_09_12': '1961-1980', 'COL16_09_12': '1981-1990',
                                    'COL17_09_12': '1991-2000', 'COL18_09_12': '2001-2005', 'COL19_09_12': '2006-2010',
                                    'COL20_09_12': '2011-2015', 'COL21_09_12': '2016-2021'})


In [504]:
# Select the data for 1940-1960, 1961-1980, 1981-1990, 1991-2000, 2001-2005, 2006-2010, 2011-2015, 2016-2021
dwelling_year = df_copy[['1940-1960', '1961-1980', '1981-1990', '1991-2000', 
                         '2001-2005', '2006-2010', '2011-2015', '2016-2021']].copy()

In [505]:
"""# Rename columns COL14_09_12: 1960, COL15_09_12: 1970, COL16_09_12: 1985, 
# COL17_09_12: 1995, COL18_09_12: 2003, COL19_09_12: 2008, COL20_09_12: 2013, COL21_09_12: 2018
# as integer values
df_copy = df_copy.rename(columns={'COL14_09_12': 1960, 'COL15_09_12': 1970, 'COL16_09_12': 1985, 
                                  'COL17_09_12': 1995, 'COL18_09_12': 2003, 'COL19_09_12': 2008, 
                                  'COL20_09_12': 2013, 'COL21_09_12': 2018})"""


"# Rename columns COL14_09_12: 1960, COL15_09_12: 1970, COL16_09_12: 1985, \n# COL17_09_12: 1995, COL18_09_12: 2003, COL19_09_12: 2008, COL20_09_12: 2013, COL21_09_12: 2018\n# as integer values\ndf_copy = df_copy.rename(columns={'COL14_09_12': 1960, 'COL15_09_12': 1970, 'COL16_09_12': 1985, \n                                  'COL17_09_12': 1995, 'COL18_09_12': 2003, 'COL19_09_12': 2008, \n                                  'COL20_09_12': 2013, 'COL21_09_12': 2018})"

In [506]:
# Select the dataframe of these columns
# dwelling_year = df_copy[[1960, 1970, 1985, 1995, 2003, 2008, 2013, 2018]].copy()

In [507]:
"""def median_frequency_distribution(series):
    # Calculate cumulative frequency
    cumulative_frequency = series.cumsum()

    # Find the median class
    total_frequency = series.sum()
    median_class = cumulative_frequency[cumulative_frequency >= total_frequency / 2].index[0]

    return median_class"""

'def median_frequency_distribution(series):\n    # Calculate cumulative frequency\n    cumulative_frequency = series.cumsum()\n\n    # Find the median class\n    total_frequency = series.sum()\n    median_class = cumulative_frequency[cumulative_frequency >= total_frequency / 2].index[0]\n\n    return median_class'

In [508]:
def median_frequency_distribution(series):
    # Ensure the input is a Pandas Series
    if not isinstance(series, pd.Series):
        raise ValueError("Input must be a Pandas Series.")

    # Convert the index to a numerical representation (e.g., the midpoint of the class)
    series.index = series.index.map(lambda x: sum(map(float, x.split('-'))) / 2)

    # Calculate cumulative frequency
    cumulative_frequency = series.sort_index().cumsum()

    # Find the median class
    total_frequency = series.sum()
    median_class = cumulative_frequency[cumulative_frequency >= total_frequency / 2].index[0]

    return median_class

In [509]:
dwelling_year.iloc[1000, :].cumsum()

1940-1960     25.0
1961-1980     70.0
1981-1990    100.0
1991-2000    180.0
2001-2005    195.0
2006-2010    210.0
2011-2015    225.0
2016-2021    255.0
Name: 1000, dtype: float64

In [510]:
median_frequency_distribution(dwelling_year.iloc[1000, :])

1995.5

In [511]:
median_frequency_distribution(dwelling_year.iloc[1, :])

2013.0

In [512]:
# dwelling_year.apply(median_frequency_distribution, axis=1)

In [513]:
# For each column in dwelling_year, fillna with the median of the column
dwelling_year = dwelling_year.apply(lambda x: x.fillna(x.median()), axis=0)
dwelling_year

1940-1960  1961-1980  1981-1990  1991-2000  2001-2005  2006-2010  \
0           0.0       30.0       95.0       10.0        0.0        0.0   
1           0.0        0.0        0.0        0.0       10.0      110.0   
2          50.0      195.0       45.0       20.0        0.0        0.0   
3         250.0       10.0        0.0        0.0        0.0        0.0   
4           0.0        0.0        0.0        0.0       10.0      110.0   
...         ...        ...        ...        ...        ...        ...   
4774      170.0       35.0        0.0        0.0        0.0        0.0   
4775      170.0       35.0        0.0        0.0        0.0        0.0   
4776       10.0      110.0      105.0        0.0        0.0        0.0   
4777       55.0       40.0       20.0       20.0       10.0        0.0   
4778        0.0        0.0        0.0       70.0       90.0       10.0   

      2011-2015  2016-2021  
0           0.0        0.0  
1         195.0        0.0  
2           0.0        0.0  
3           0.0        0.0  
4         195.0        0.0  
...         ...        ...  
4774       10.0        0.0  
4775        0.0       15.0  
4776        0.0        0.0  
4777        0.0        0.0  
4778        0.0        0.0  

[4779 rows x 8 columns]

In [514]:
# Apply the median_frequency_distribution function to each row in dwelling_year using a for loop
median_year = []
for idx, row in dwelling_year.iterrows():
    median_year.append(median_frequency_distribution(row))

# Add the median_year list as a new column to df_copy
df_copy['Median_year'] = median_year

In [515]:
df_copy['Median_year'] 

0       1985.5
1       2013.0
2       1970.5
3       1950.0
4       2013.0
         ...  
4774    1950.0
4775    1950.0
4776    1970.5
4777    1970.5
4778    2003.0
Name: Median_year, Length: 4779, dtype: float64

In [516]:
df_copy['Median_year'].value_counts()


1970.5    2428
1950.0     731
1985.5     318
2013.0     307
2008.0     297
1995.5     286
2003.0     266
2018.5     146
Name: Median_year, dtype: int64

In [517]:
df_copy['Apartment percentage'] = (df_copy['COL9_09_12'] + df_copy['COL10_09_12']) / df_copy['COL4_09_12']
df_copy['Apartment percentage'].fillna(df_copy['Apartment percentage'].median(), inplace=True)

In [518]:
df_copy.dauid.isna().sum()

1548

Below are the Pcodes that remain unassociated with a census DA

In [519]:
# Show the pcode of df_copy dauids with nan values
df_copy[df_copy['dauid'].isna()]['pcode'].unique()

array(['L6G9R2', 'M9N0B6', nan, 'M4YBDBD', 'L4A', 'M6K', 'L7R', 'M4M',
       'M5C', 'M1K', 'L6R', 'L1R7R5', 'L1S5E4,', 'L6JL7L', 'M6N4B',
       'M5AON3', 'M1L', 'M5V4K8', 'L6C', 'L4J1B', 'L831C7', 'M5A54E8',
       'MIV2Z6', 'M8Y', 'M5V', 'L5N2G7A', 'M8V', 'M1CC1Z', 'M1W', 'M6C',
       'L3T', 'LL8B1W5', 'M4Y', 'L8JOL8', 'M4C0J5'], dtype=object)

Adding these additional columns to df_reduced

In [520]:
# Include in df_reduced and save to excel
df_reduced = df_reduced.merge(df_copy[['Car_driver_mode_share', 'Car_passenger_mode_share', 'Public_transit_mode_share', 'Walk_mode_share', 'Bike_mode_share', 
                                       'Log_median_rent', 'Log_average_rent', 'Log_median_mortgage', 'Log_average_mortgage', 
                                       'Apartment percentage', 'Median_year', 'Popn_density']], left_index=True, right_index=True, how='left')
# df_reduced.dropna(inplace=True)



In [521]:
# Rename Q13 and Q3_11
df_reduced = df_reduced.rename(columns={'Q13': 'Log_income', 'Q3_11': 'Household_size'})

In [522]:
df_reduced.isna().sum()

Log_income                                0
Household_size                            0
Q14_12                                 1547
Q8                                     1548
Medium_number                             0
Small_number                              0
Off_road_number                           0
Luxury_number                             0
Van_number                                0
Distance_to_scotiabank_tower           1714
Number_cars                            1582
Gasoline                                  0
Residential_underground_number            0
Garage_number                             0
Surface_lot_number                        0
Residential_on_street_number              0
Indoor_public_number                      0
Parking_cost_per_slot                     0
Distance_to_closest_subway_station        0
Length_of_cycle_lanes_within_radius    1714
Distance_to_closest_bus_station        1871
Number_cars_level                      1582
Log_distance_to_scotia_plaza    

In [523]:
# Fill in Car_driver_mode_share, Car_passenger_mode_share, Public_transit_mode_share, Walk_mode_share and Bike_mode_share with the mean of the column
df_reduced['Car_driver_mode_share'].fillna(df_reduced['Car_driver_mode_share'].mean(), inplace=True)
df_reduced['Car_passenger_mode_share'].fillna(df_reduced['Car_passenger_mode_share'].mean(), inplace=True)
df_reduced['Public_transit_mode_share'].fillna(df_reduced['Public_transit_mode_share'].mean(), inplace=True)
df_reduced['Walk_mode_share'].fillna(df_reduced['Walk_mode_share'].mean(), inplace=True)
df_reduced['Bike_mode_share'].fillna(df_reduced['Bike_mode_share'].mean(), inplace=True)

Trying to deal with the 'not all response levels are observed. Model might be non-identifiable if
          the thresholds for this response are not restricted.' error

In [524]:
# Dataframe of value_counts for Medium_number, Small_number, Off_road_number, Luxury_number, Van_number
df_reduced[['Medium_number', 'Small_number', 'Off_road_number', 'Luxury_number', 'Van_number']].apply(pd.Series.value_counts)

Medium_number  Small_number  Off_road_number  Luxury_number  Van_number
0           3120          4153             4489           4611      4521.0
1           1319           563              258            146       237.0
2            317            62               30             20        21.0
3             23             1                2              2         NaN

In [525]:
# Total number of each type of car from df_reduced
df_reduced[['Medium_number', 'Small_number', 'Off_road_number', 'Luxury_number', 'Van_number']].sum()

Medium_number      2022
Small_number        690
Off_road_number     324
Luxury_number       192
Van_number          279
dtype: int64

In [526]:
# Create new columns, Medium_number_restricted, Small_number_restricted, Off_road_number_restricted, Luxury_number_restricted, Van_number_restricted that are 2 if the number of cars >=2, and takes the original value if the number of cars < 2
df_reduced['Medium_number_restricted'] = df_reduced['Medium_number'].apply(lambda x: 2 if x >= 2 else x)
df_reduced['Small_number_restricted'] = df_reduced['Small_number'].apply(lambda x: 2 if x >= 2 else x)
df_reduced['Off_road_number_restricted'] = df_reduced['Off_road_number'].apply(lambda x: 2 if x >= 2 else x)
df_reduced['Luxury_number_restricted'] = df_reduced['Luxury_number'].apply(lambda x: 2 if x >= 2 else x)
df_reduced['Van_number_restricted'] = df_reduced['Van_number'].apply(lambda x: 2 if x >= 2 else x)

In [527]:
# Dataframe of value_counts for Medium_number_restricted, Small_number_restricted, Off_road_number_restricted, Luxury_number_restricted, Van_number_restricted
df_reduced[['Medium_number_restricted', 'Small_number_restricted', 'Off_road_number_restricted', 'Luxury_number_restricted', 'Van_number_restricted']].apply(pd.Series.value_counts)


Medium_number_restricted  Small_number_restricted  \
0                      3120                     4153   
1                      1319                      563   
2                       340                       63   

   Off_road_number_restricted  Luxury_number_restricted  Van_number_restricted  
0                        4489                      4611                   4521  
1                         258                       146                    237  
2                          32                        22                     21

# Save

In [528]:
# df_reduced.to_excel(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\IATBR\R_code\Sign-Up_ordered_f.xlsx', index=False)
df_reduced.to_excel(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\WSTLUR 2023\Sign-Up_ordered_wsltur2.xlsx', index=False)

In [529]:
# Pickling as well
df_reduced.to_pickle(r'C:\Users\mwendwa.kiko\Documents\Personal_Kiko\UofT\Research\WSTLUR 2023\Sign-Up_ordered_wsltur2.pkl')

In [532]:
df_reduced.columns

Index(['Log_income', 'Household_size', 'Q14_12', 'Q8', 'Medium_number',
       'Small_number', 'Off_road_number', 'Luxury_number', 'Van_number',
       'Distance_to_scotiabank_tower', 'Number_cars', 'Gasoline',
       'Residential_underground_number', 'Garage_number', 'Surface_lot_number',
       'Residential_on_street_number', 'Indoor_public_number',
       'Parking_cost_per_slot', 'Distance_to_closest_subway_station',
       'Length_of_cycle_lanes_within_radius',
       'Distance_to_closest_bus_station', 'Number_cars_level',
       'Log_distance_to_scotia_plaza', 'Car_driver_mode_share',
       'Car_passenger_mode_share', 'Public_transit_mode_share',
       'Walk_mode_share', 'Bike_mode_share', 'Log_median_rent',
       'Log_average_rent', 'Log_median_mortgage', 'Log_average_mortgage',
       'Apartment percentage', 'Median_year', 'Popn_density',
       'Medium_number_restricted', 'Small_number_restricted',
       'Off_road_number_restricted', 'Luxury_number_restricted',
       'Van_